In [1]:
import sys
sys.path.append('/Users/bhargavdesai/Desktop/IU/RA/CNS/hra-amap/code')

from organ import Organ
from tissue import TissueBlock
from pipeline import Pipeline
from dataclass import Projection
from utils.conversions import to_pointcloud


import time
import trimesh
import numpy as np
import ccf_openapi_client

from ccf_openapi_client.api import default_api
from copy import deepcopy
from tqdm.auto import tqdm

##### Set up the CCF API

In [2]:
configuration = ccf_openapi_client.Configuration(
    host = "https://ccf-api.hubmapconsortium.org/v1"
)

api_client = ccf_openapi_client.ApiClient(configuration)
api_instance = default_api.DefaultApi(api_client)

##### Connect to Database

In [3]:
db_ready = False
result = None
while not db_ready:
    result = api_instance.db_status()
    if result['status'] == 'Ready':
        db_ready = True
    else:
        print('Database not ready yet! Retrying...', result)
        time.sleep(2)
print('Database ready!\n', result)

Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retrying... {'checkback': 2000, 'message': 'Loading database', 'status': 'Loading'}
Database not ready yet! Retr

##### Download Registered Tissue Block Data

In [4]:
try:
    api_response = api_instance.hubmap_rui_locations(cache=True)
except ccf_openapi_client.ApiException as e:
    print("Exception when calling DefaultApi->aggregate_results: %s\n" % e)

##### Filter Tissue Blocks

In [19]:
def filter(data, filter):
  filtered = []
  for donor in tqdm(data):
    filtered_samples = []
    for sample in donor['samples']:
      # get the organ the current sample is registered to
      target = sample['rui_location']['placement']['target'].split('#')[-1]
      # filter
      filter_str = ''.join([filter['gender'], filter['laterality'], filter['name']])
      if filter['version'] == 'All':
        if filter_str in target:
          filtered_samples.append(sample)
      if filter['version'] == 'Latest':
        if filter_str == target:
          filtered_samples.append(sample)
      else:
        filter_str = filter_str + filter['version']
        if filter_str == target:
          filtered_samples.append(sample)
    # add to filtered if valid samples are found
    if filtered_samples:
      donor['samples'] = filtered_samples
      filtered.append(donor)
  
  return filtered

In [20]:
organ = {'name': 'Kidney', 
         'gender': 'VHF', 
         'laterality': 'Right', 
         'version': 'V1.1'}

In [21]:
result = filter(deepcopy(api_response['@graph']), organ)

  0%|          | 0/140 [00:00<?, ?it/s]

##### Create `TissueBlock`(s)

In [22]:
tissue_blocks = []
target_name = 'VHFRightKidneyV1.1'

for donor in result:
    blocks = [TissueBlock.from_sample(sample, donor, target_name) for sample in donor['samples']]
    tissue_blocks.extend(blocks)

In [23]:
print(f'Found {len(tissue_blocks)} Tissue Blocks')

Found 13 Tissue Blocks


##### Project

In [24]:
# load saved projections (replace this with the saved projections path)
projections = Projection.load('/Users/bhargavdesai/Desktop/IU/RA/CNS/Paper Results/Projections/Backward/VHF_RightKidney_to_VU500RightKidney_v2-e25b6674-fbdc-43d9-b0b2-ee0d886d144e/projections.pickle')

In [25]:
# project
projected_blocks = [projections.project(block) for block in deepcopy(tissue_blocks)]

# create an oriented bounding box around the projected blocks
projected_blocks = [block.bounding_box_oriented for block in projected_blocks]

##### Visualization

In [26]:
# colors
mustard = np.array([225, 173, 1, 255], dtype=np.uint8)
reddishpink = np.array([222, 49, 99, 100], dtype=np.uint8)

In [27]:
# load source organ
source = Organ(path='../data/Kidney/Reference/VH_F_Kidney_R.glb')

# concatenate original tissue blocks before displaying (for efficiency reasons)
tissue_blocks_concatenated = trimesh.util.concatenate(tissue_blocks)

# add color
source.visual.vertex_colors = reddishpink
tissue_blocks_concatenated.visual.vertex_colors = mustard

# create scene with the blocks on the source organ
source_with_tbs = trimesh.Scene([source, tissue_blocks_concatenated])

# show
source_with_tbs.show()

In [28]:
# load the target organ
target = Organ(path='../data/Kidney/Source/atlasSeg_rk.vtk')

# concatenate original tissue blocks before displaying (for efficiency reasons)
projected_blocks_concatenated = deepcopy(trimesh.util.concatenate(projected_blocks))

# add color
target.visual.vertex_colors = reddishpink
projected_blocks_concatenated.visual.vertex_colors = mustard

In [29]:
# create scene with the blocks on the target organ
target_with_tbs = trimesh.Scene([target, projected_blocks_concatenated])

# show
target_with_tbs.show()